<h1><span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Setup-Environment" data-toc-modified-id="Setup-Environment-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Setup Environment</a></span><ul class="toc-item"><li><span><a href="#Install-Libraries" data-toc-modified-id="Install-Libraries-1.1"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>Install Libraries</a></span></li><li><span><a href="#Import-Libraries" data-toc-modified-id="Import-Libraries-1.2"><span class="toc-item-num">1.2&nbsp;&nbsp;</span>Import Libraries</a></span></li><li><span><a href="#Global-Display-Setting" data-toc-modified-id="Global-Display-Setting-1.3"><span class="toc-item-num">1.3&nbsp;&nbsp;</span>Global Display Setting</a></span></li><li><span><a href="#Global-Constants" data-toc-modified-id="Global-Constants-1.4"><span class="toc-item-num">1.4&nbsp;&nbsp;</span>Global Constants</a></span></li><li><span><a href="#Random-Seed" data-toc-modified-id="Random-Seed-1.5"><span class="toc-item-num">1.5&nbsp;&nbsp;</span>Random Seed</a></span></li></ul></li><li><span><a href="#Exploratory-Data-Analysis" data-toc-modified-id="Exploratory-Data-Analysis-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Exploratory Data Analysis</a></span><ul class="toc-item"><li><span><a href="#Loading-Data" data-toc-modified-id="Loading-Data-2.1"><span class="toc-item-num">2.1&nbsp;&nbsp;</span>Loading Data</a></span></li><li><span><a href="#Features-Analysis" data-toc-modified-id="Features-Analysis-2.2"><span class="toc-item-num">2.2&nbsp;&nbsp;</span>Features Analysis</a></span><ul class="toc-item"><li><span><a href="#Features--Type" data-toc-modified-id="Features--Type-2.2.1"><span class="toc-item-num">2.2.1&nbsp;&nbsp;</span>Features  Type</a></span></li><li><span><a href="#Univariate-and-Multivariate-Visulizations" data-toc-modified-id="Univariate-and-Multivariate-Visulizations-2.2.2"><span class="toc-item-num">2.2.2&nbsp;&nbsp;</span>Univariate and Multivariate Visulizations</a></span></li></ul></li><li><span><a href="#Targets-Analysis-(Multi-Label-Classification)" data-toc-modified-id="Targets-Analysis-(Multi-Label-Classification)-2.3"><span class="toc-item-num">2.3&nbsp;&nbsp;</span>Targets Analysis (Multi Label Classification)</a></span></li></ul></li></ul></div>

In [1]:
! [ ! -L /kaggle ] && ln -s /data/kaggle /kaggle 

[geekysaint/demystifying-mechanism-of-action-eda][1]

[1]: https://www.kaggle.com/geekysaint/demystifying-mechanism-of-action-eda

## Setup Environment

### Install Libraries 

In [2]:
import pkg_resources

LIBS = sorted(pkg_resources.working_set)

needed_stack = [
    'numpy', 'pandas', 'seaborn', 'matplotlib',
    'torch', 'torchvision', 'scikit-learn', 'plotly',
    'iterative-stratification', 'pytorch-lightning'
]

for item in LIBS:
    if item.project_name in needed_stack:
        print(item.project_name, item.version)
        needed_stack.remove(item.project_name)
for apk in needed_stack:
    !pip install $apk

iterative-stratification 0.1.6
torchvision 0.7.0.dev20200609+cu101
pytorch-lightning 0.9.0
seaborn 0.10.1
scikit-learn 0.23.1
pandas 1.0.4
torch 1.6.0.dev20200609+cu101
numpy 1.18.5
matplotlib 3.2.1
plotly 4.10.0


### Import Libraries

In [3]:
import os
import warnings
import random
import pytorch_lightning as pl
import numpy as np
import pandas as pd
import seaborn as sns
import torch
import torchvision
import plotly.express as px
import plotly.graph_objects as go
import matplotlib.pyplot as plt

from torch import nn
from torch.nn import functional as F
from torch.utils.data import (Dataset, DataLoader)
from torchvision.transforms import (
        Resize,
        Compose,
        ToTensor,
        Normalize,
        RandomOrder,
        ColorJitter,
        RandomRotation,
        RandomGrayscale,
        RandomResizedCrop,
        RandomVerticalFlip,
        RandomHorizontalFlip)

from PIL import Image, ImageDraw, ImageFont
from sklearn.model_selection import train_test_split
from pytorch_lightning.callbacks import EarlyStopping
from pytorch_lightning.callbacks import ModelCheckpoint
from plotly.subplots import make_subplots

### Global Display Setting

In [4]:
%matplotlib inline

warnings.filterwarnings("ignore")

pd.set_option('display.float_format', lambda x: '{:.3f}'.format(x))
pd.set_option('display.max_columns', 30)

# sns.set(style='white', font_scale=1.2)

### Global Constants

In [5]:
RNG_SEED = 9527
DATA_NAME = 'lish-moa'
DATA_ROOT = f'/kaggle/input/{DATA_NAME}'
WORK_ROOT = f'/kaggle/working/{DATA_NAME}'
CKPT_PATH = f'{WORK_ROOT}/checkpoints/best.ckpt'
SUBMITCSV = '/kaggle/working/submission.csv'
FONT_PATH = '/usr/share/fonts/truetype/dejavu/DejaVuSerif-Bold.ttf'

INPUT_SIZE = 28
BATCH_SIZE = 48
NUM_CLASSES = 10

MAX_EPOCHS = 30

TEST_SPLIT = 0.3

### Random Seed

In [6]:
torch.manual_seed(RNG_SEED)
torch.cuda.manual_seed(RNG_SEED)
np.random.seed(RNG_SEED)
random.seed(RNG_SEED)

torch.backends.cudnn.deterministic = True
torch.backends.cudnn.benchmark = False

In [7]:
!ls -l $DATA_ROOT
!mkdir -p $WORK_ROOT

total 210376
-rw-rw-r-- 1 1002 1002   3337770 Sep  2 15:04 sample_submission.csv
-rw-rw-r-- 1 1002 1002  26140860 Sep  2 15:04 test_features.csv
-rw-rw-r-- 1 1002 1002 156340282 Sep  2 15:04 train_features.csv
-rw-rw-r-- 1 1002 1002  19466300 Sep  2 15:04 train_targets_nonscored.csv
-rw-rw-r-- 1 1002 1002  10125786 Sep  2 15:04 train_targets_scored.csv


##  Exploratory Data Analysis

### Loading Data

In [8]:
df_train_features = pd.read_csv(os.path.join(DATA_ROOT, 'train_features.csv'))
df_train_targets  = pd.read_csv(os.path.join(DATA_ROOT, 'train_targets_scored.csv'))
df_test_features  = pd.read_csv(os.path.join(DATA_ROOT, 'test_features.csv'))

df_train_features.shape, df_train_targets.shape, df_test_features.shape

((23814, 876), (23814, 207), (3982, 876))

In [9]:
feature_names = df_train_features.columns[1:] 
target_names  = df_train_targets.columns[1:]

In [10]:
df_train_features.head()

sig_id cp_type  cp_time cp_dose    g-0    g-1    g-2    g-3    g-4  \
0  id_000644bb2  trt_cp       24      D1  1.062  0.558 -0.248 -0.621 -0.194   
1  id_000779bfc  trt_cp       72      D1  0.074  0.409  0.299  0.060  1.019   
2  id_000a6266a  trt_cp       48      D1  0.628  0.582  1.554 -0.076 -0.032   
3  id_0015fd391  trt_cp       48      D1 -0.514 -0.249 -0.266  0.529  4.062   
4  id_001626bd3  trt_cp       72      D2 -0.325 -0.401  0.970  0.692  1.418   

     g-5    g-6    g-7    g-8    g-9   g-10  ...   c-85   c-86   c-87   c-88  \
0 -1.012 -1.022 -0.033  0.555 -0.092  1.183  ...  0.180  0.537 -0.111 -1.012   
1  0.521  0.234  0.337 -0.405  0.851 -1.152  ...  0.442  0.937  0.819 -0.424   
2  1.239  0.172  0.215  0.006  1.230 -0.480  ...  0.117  0.109 -0.311  0.302   
3 -0.809 -1.959  0.179 -0.132 -1.060 -0.827  ... -1.539 -2.460 -0.942 -1.555   
4 -0.824 -0.280 -0.150 -0.879  0.863 -0.222  ...  0.070  0.813  0.192  0.605   

    c-89   c-90   c-91   c-92   c-93   c-94   c-95   c-96   c-97   c-98   c-99  
0  0.668  0.286  0.258  0.808  0.552 -0.191  0.658 -0.398  0.214  0.380  0.418  
1  0.319 -0.426  0.754  0.471  0.023  0.296  0.490  0.152  0.124  0.608  0.737  
2 -0.087 -0.725 -0.630  0.610  0.022 -1.324 -0.317 -0.642 -0.219 -1.408  0.693  
3  0.243 -2.099 -0.644 -5.630 -1.378 -0.863 -1.288 -1.621 -0.878 -0.388 -0.815  
4 -0.182  0.004  0.005  0.667  1.069  0.552 -0.303  0.109  0.288 -0.379  0.713  

[5 rows x 876 columns]

In [11]:
mask_smaples = (df_train_targets[target_names[0]] > 0) | (df_train_targets[target_names[2]] > 0)
df_train_targets.loc[mask_smaples].tail()

sig_id  5-alpha_reductase_inhibitor  11-beta-hsd1_inhibitor  \
19382  id_d00440fe6                            0                       0   
19571  id_d218733b4                            0                       0   
20100  id_d7bb3adc4                            1                       0   
21941  id_eb64d285a                            1                       0   
23146  id_f89e49084                            1                       0   

       acat_inhibitor  acetylcholine_receptor_agonist  \
19382               1                               0   
19571               1                               0   
20100               0                               0   
21941               0                               0   
23146               0                               0   

       acetylcholine_receptor_antagonist  acetylcholinesterase_inhibitor  \
19382                                  0                               0   
19571                                  0                               0   
20100                                  0                               0   
21941                                  0                               0   
23146                                  0                               0   

       adenosine_receptor_agonist  adenosine_receptor_antagonist  \
19382                           0                              0   
19571                           0                              0   
20100                           0                              0   
21941                           0                              0   
23146                           0                              0   

       adenylyl_cyclase_activator  adrenergic_receptor_agonist  \
19382                           0                            0   
19571                           0                            0   
20100                           0                            0   
21941                           0                            0   
23146                           0                            0   

       adrenergic_receptor_antagonist  akt_inhibitor  \
19382                               0              0   
19571                               0              0   
20100                               0              0   
21941                               0              0   
23146                               0              0   

       aldehyde_dehydrogenase_inhibitor  alk_inhibitor  ...  tlr_agonist  \
19382                                 0              0  ...            0   
19571                                 0              0  ...            0   
20100                                 0              0  ...            0   
21941                                 0              0  ...            0   
23146                                 0              0  ...            0   

       tlr_antagonist  tnf_inhibitor  topoisomerase_inhibitor  \
19382               0              0                        0   
19571               0              0                        0   
20100               0              0                        0   
21941               0              0                        0   
23146               0              0                        0   

       transient_receptor_potential_channel_antagonist  \
19382                                                0   
19571                                                0   
20100                                                0   
21941                                                0   
23146                                                0   

       tropomyosin_receptor_kinase_inhibitor  trpv_agonist  trpv_antagonist  \
19382                                      0             0                0   
19571                                      0             0                0   
20100                                      0             0                0   
21941                                      0             0                0   
23146                

### Features Analysis

In [12]:
df_train_features.describe()

cp_time       g-0       g-1       g-2       g-3       g-4       g-5  \
count 23814.000 23814.000 23814.000 23814.000 23814.000 23814.000 23814.000   
mean     48.020     0.248    -0.096     0.152     0.082     0.057    -0.139   
std      19.403     1.393     0.812     1.036     0.950     1.032     1.179   
min      24.000    -5.513    -5.737    -9.104    -5.998    -6.369   -10.000   
25%      24.000    -0.473    -0.562    -0.438    -0.430    -0.471    -0.602   
50%      48.000    -0.009    -0.047     0.075     0.008    -0.027    -0.016   
75%      72.000     0.526     0.403     0.664     0.463     0.465     0.510   
max      72.000    10.000     5.039     8.257    10.000    10.000     7.282   

            g-6       g-7       g-8       g-9      g-10      g-11      g-12  \
count 23814.000 23814.000 23814.000 23814.000 23814.000 23814.000 23814.000   
mean      0.036    -0.203    -0.190     0.120    -0.123     0.182     0.143   
std       0.882     1.125     1.750     1.087     1.292     1.254     1.235   
min     -10.000   -10.000   -10.000    -8.337   -10.000    -5.870    -8.587   
25%      -0.494    -0.525    -0.512    -0.360    -0.511    -0.490    -0.448   
50%      -0.001    -0.018     0.010     0.160     0.039     0.014     0.060   
75%       0.529     0.412     0.549     0.698     0.525     0.575     0.604   
max       7.333     5.473     8.887     6.433    10.000    10.000    10.000   

           g-13  ...      c-85      c-86      c-87      c-88      c-89  \
count 23814.000  ... 23814.000 23814.000 23814.000 23814.000 23814.000   
mean      0.209  ...    -0.409    -0.333    -0.295    -0.328    -0.402   
std       1.273  ...     1.884     1.647     1.634     1.663     1.833   
min      -5.018  ...   -10.000   -10.000   -10.000   -10.000   -10.000   
25%      -0.481  ...    -0.560    -0.534    -0.505    -0.544    -0.569   
50%       0.010  ...    -0.002     0.008    -0.006    -0.021    -0.030   
75%       0.576  ...     0.462     0.466     0.463     0.450     0.431   
max      10.000  ...     3.738     3.252     5.406     3.110     3.320   

           c-90      c-91      c-92      c-93      c-94      c-95      c-96  \
count 23814.000 23814.000 23814.000 23814.000 23814.000 23814.000 23814.000   
mean     -0.469    -0.461    -0.513    -0.500    -0.507    -0.354    -0.463   
std       2.000     2.042     2.002     2.107     2.160     1.629     2.060   
min     -10.000   -10.000   -10.000   -10.000   -10.000   -10.000   -10.000   
25%      -0.566    -0.566    -0.590    -0.569    -0.564    -0.568    -0.553   
50%      -0.010     0.003    -0.009    -0.014    -0.003    -0.010    -0.001   
75%       0.458     0.462     0.446     0.453     0.471     0.445     0.465   
max       4.069     3.960     3.927     3.596     3.747     2.814     3.505   

           c-97      c-98      c-99  
count 23814.000 23814.000 23814.000  
mean     -0.378    -0.470    -0.302  
std       1.704     1.835     1.408  
min     -10.000   -10.000   -10.000  
25%      -0.561    -0.593    -0.563  
50%      -0.007     0.014    -0.019  
75%       0.446     0.461     0.439  
max       2.924     3.111     3.805  

[8 rows x 873 columns]

#### Features  Type

In [13]:
df_category_features  = df_train_features.select_dtypes(include=['object'])
df_numerical_features = df_train_features.select_dtypes(exclude=['object'])
set([str(x) for x in df_category_features.dtypes.values]), \
set([str(x) for x in df_numerical_features.dtypes.values])

({'object'}, {'float64', 'int64'})

In [14]:
df_category_features.columns.to_list()

['sig_id', 'cp_type', 'cp_dose']

In [15]:
df_int64_features = df_train_features.select_dtypes(include=['int64'])
for col in df_int64_features.columns:
    if len(df_int64_features[col].value_counts()) < 10: # TODO
        df_category_features[col] = df_int64_features[col]
        df_numerical_features.drop([col], axis=1, inplace=True)

In [16]:
df_category_features.drop(['sig_id'], axis=1, inplace=True)
df_category_features.columns.to_list()

['cp_type', 'cp_dose', 'cp_time']

#### Univariate and Multivariate Visulizations 

In [35]:
fig = make_subplots(
    rows=1, cols=3,
    subplot_titles=("Type(Compound vs Control)", "Time(in Hours)", "Dose(High vs Low)")
)

fig.update_layout(title_text = "Train Data Features")
fig.update_yaxes(title_text="Total Observations in the Dataset", row=1, col=1)
fig.layout.template = 'plotly_dark'
fig.update_layout(title_text = "Train dataset Features")

for idx, name in enumerate(df_category_features.columns, 1):
    # df_category_features[col].value_counts().plot(kind='bar',figsize=[10,3], title=col)
    # plt.show()
    series = df_category_features[name].value_counts()
    fig.add_trace(
        go.Bar(
            x=series.index, y=series.values,
            text=series.values,
            textposition="outside",
            name=name),
        row=1, col=idx)
    fig.update_xaxes(title_text=name, row=1, col=idx)

fig.show()

In [61]:
GENES = [col for col in df_numerical_features.columns if col.startswith('g-')]
CELLS = [col for col in df_numerical_features.columns if col.startswith('c-')]

nrow = 6
ncol = 2

def random_visualiz(df, features, title, nrow, ncol):
    samples = random.sample(features, nrow*ncol)

    fig = make_subplots(
        rows=nrow, cols=ncol,
        subplot_titles=samples
    )

    fig.layout.template = 'plotly_dark'
    fig.update_layout(showlegend=False, title_text=title)

    for r in range(nrow):
        for c in range(ncol):
            name = samples[r*ncol + c]
            fig.add_trace(
                go.Histogram(
                    x=df[name].values,
                    name=name),
                row=r+1, col=c+1)
    fig.show()
    
random_visualiz(
    df_numerical_features,
    GENES, 'Sample of Genes Distribution',
    nrow, ncol,
)

random_visualiz(
    df_numerical_features,
    CELLS, 'Sample of Cells Distribution',
    nrow, ncol,
)

### Targets Analysis (Multi Label Classification)

In [ ]:
df_train_targets.describe()